## Import Libraries

In [1]:
#IMPORT LIBRARIES
!pip install folium
!pip install geopy
!pip install beautifulsoup4
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt
import seaborn as sns
import requests
from bs4 import BeautifulSoup 
%matplotlib inline

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

     |████████████████████████████████| 102kB 7.3MB/s ta 0:00:011
Libraries imported.


## Bring in Toronto wiki data from Lab

In [2]:
#Bring in Toronto Wiki Data
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
tor_url = requests.get(url)
tor_url


<Response [200]>

## Read Toronto Wiki Data into Pandas DF

In [3]:
#read wiki data
tor_data = pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')[0]

tor_data.rename(columns={"Post Code": "Postal Code"}, inplace=True)
tor_data

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
5           M6A        North York   
6           M7A  Downtown Toronto   
7           M8A      Not assigned   
8           M9A         Etobicoke   
9           M1B       Scarborough   
10          M2B      Not assigned   
11          M3B        North York   
12          M4B         East York   
13          M5B  Downtown Toronto   
14          M6B        North York   
15          M7B      Not assigned   
16          M8B      Not assigned   
17          M9B         Etobicoke   
18          M1C       Scarborough   
19          M2C      Not assigned   
20          M3C        North York   
21          M4C         East York   
22          M5C  Downtown Toronto   
23          M6C              York   
24          M7C      Not assigned   
25          M8C      Not assigned   
26          M9C         Etobicoke   
27          M1E       Scarborough   
28          M2E      Not assigned   
29          M3E      Not assigned   
30          M4E      East Toronto   
31          M5E  Downtown Toronto   
32          M6E              York   
33          M7E      Not assigned   
34          M8E      Not assigned   
35          M9E      Not assigned   
36          M1G       Scarborough   
37          M2G      Not assigned   
38          M3G      Not assigned   
39          M4G         East York   
40          M5G  Downtown Toronto   
41          M6G  Downtown Toronto   
42          M7G      Not assigned   
43          M8G      Not assigned   
44          M9G      Not assigned   
45          M1H       Scarborough   
46          M2H        North York   
47          M3H        North York   
48          M4H         East York   
49          M5H  Downtown Toronto   
50          M6H      West Toronto   
51          M7H      Not assigned   
52          M8H      Not assigned   
53          M9H      Not assigned   
54          M1J       Scarborough   
55          M2J        North York   
56          M3J        North York   
57          M4J         East York   
58          M5J  Downtown Toronto   
59          M6J      West Toronto   
60          M7J      Not assigned   
61          M8J      Not assigned   
62          M9J      Not assigned   
63          M1K       Scarborough   
64          M2K        North York   
65          M3K        North York   
66          M4K      East Toronto   
67          M5K  Downtown Toronto   
68          M6K      West Toronto   
69          M7K      Not assigned   
70          M8K      Not assigned   
71          M9K      Not assigned   
72          M1L       Scarborough   
73          M2L        North York   
74          M3L        North York   
75          M4L      East Toronto   
76          M5L  Downtown Toronto   
77          M6L        North York   
78          M7L      Not assigned   
79          M8L      Not assigned   
80          M9L        North York   
81          M1M       Scarborough   
82          M2M        North York   
83          M3M        North York   
84          M4M      East Toronto   
85          M5M        North York   
86          M6M              York   
87          M7M      Not assigned   
88          M8M      Not assigned   
89          M9M        North York   
90          M1N       Scarborough   
91          M2N        North York   
92          M3N        North York   
93          M4N   Central Toronto   
94          M5N   Central Toronto   
95          M6N              York   
96          M7N      Not assigned   
97          M8N      Not assigned   
98          M9N              York   
99          M1P       Scarborough   
100         M2P        North York   
101         M3P      Not assigned   
102         M4P   Central Toronto   
103         M5P   Central Toronto   
104         M6P      West Toronto   
105         M7P      Not assigned   
106         M8P      Not assigned   
107     

## Look at shape and counts of data

In [4]:
tor_data.shape

(180, 3)

In [5]:
tor_data.Borough.value_counts()

Not assigned        77
North York          24
Downtown Toronto    19
Scarborough         17
Etobicoke           12
Central Toronto      9
West Toronto         6
East York            5
York                 5
East Toronto         5
Mississauga          1
Name: Borough, dtype: int64

## Drop NA the instructions for this are wrong there are no duplicate postal codes that need combined

In [6]:
borough_na = tor_data[tor_data.Borough == 'Not assigned']
tor_data.drop(borough_na.index, inplace=True)
tor_data
tor_data.shape

(103, 3)

In [7]:
tor_data.shape

(103, 3)

##  Bring in Long and Lat from CSV file provided in Lab

In [10]:
#Phase2 
geo_url = "https://cocl.us/Geospatial_data"

geocode_df = pd.read_csv(geo_url) 
geocode_df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

## Merge File with Long and Lat

In [11]:
tor_data = pd.merge(tor_data, geocode_df, how = 'right', on='Postal Code')
tor_data.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

## Review shape

In [72]:
tor_data.shape

(103, 5)

## Look at only boroughs that contain Toronto

In [74]:
tor_data2 = tor_data[tor_data['Borough'].str.contains('Toronto', na = False).reset_index(drop=True)]
tor_data2.head()

Postal Code           Borough                                Neighbourhood  \
2          M5A  Downtown Toronto                    Regent Park, Harbourfront   
4          M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   
9          M5B  Downtown Toronto                     Garden District, Ryerson   
15         M5C  Downtown Toronto                               St. James Town   
19         M4E      East Toronto                                  The Beaches   

     Latitude  Longitude  
2   43.654260 -79.360636  
4   43.662301 -79.389494  
9   43.657162 -79.378937  
15  43.651494 -79.375418  
19  43.676357 -79.293031

## Look at shape

In [75]:
tor_data2.shape

(39, 5)

In [76]:
tor_data2.dtypes

Postal Code       object
Borough           object
Neighbourhood     object
Latitude         float64
Longitude        float64
dtype: object

## rename neighborhood every time I pull this from wiki neighborhood and postal code have a diff spelling

In [77]:
tor_data2.rename(columns= {'Neighbourhood':'Neighborhood'}, inplace = True)

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:4025: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  return super(DataFrame, self).rename(**kwargs)


## Drop last rown since it has no restaurant outouts

In [93]:
tor_data2.drop(tor_data2.index[-1], inplace = True)
tor_data2

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


Postal Code           Borough  \
2          M5A  Downtown Toronto   
4          M7A  Downtown Toronto   
9          M5B  Downtown Toronto   
15         M5C  Downtown Toronto   
19         M4E      East Toronto   
20         M5E  Downtown Toronto   
24         M5G  Downtown Toronto   
25         M6G  Downtown Toronto   
30         M5H  Downtown Toronto   
31         M6H      West Toronto   
36         M5J  Downtown Toronto   
37         M6J      West Toronto   
41         M4K      East Toronto   
42         M5K  Downtown Toronto   
43         M6K      West Toronto   
47         M4L      East Toronto   
48         M5L  Downtown Toronto   
54         M4M      East Toronto   
61         M4N   Central Toronto   
62         M5N   Central Toronto   
67         M4P   Central Toronto   
68         M5P   Central Toronto   
69         M6P      West Toronto   
73         M4R   Central Toronto   
74         M5R   Central Toronto   
75         M6R      West Toronto   
79         M4S   Central Toronto   
80         M5S  Downtown Toronto   
81         M6S      West Toronto   
83         M4T   Central Toronto   
84         M5T  Downtown Toronto   
86         M4V   Central Toronto   
87         M5V  Downtown Toronto   
91         M4W  Downtown Toronto   
92         M5W  Downtown Toronto   
96         M4X  Downtown Toronto   
97         M5X  Downtown Toronto   
99         M4Y  Downtown Toronto   

                                         Neighborhood   Latitude  Longitude  
2                           Regent Park, Harbourfront  43.654260 -79.360636  
4         Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
9                            Garden District, Ryerson  43.657162 -79.378937  
15                                     St. James Town  43.651494 -79.375418  
19                                        The Beaches  43.676357 -79.293031  
20                                        Berczy Park  43.644771 -79.373306  
24                                 Central Bay Street  43.657952 -79.387383  
25                                           Christie  43.669542 -79.422564  
30                           Richmond, Adelaide, King  43.650571 -79.384568  
31                       Dufferin, Dovercourt Village  43.669005 -79.442259  
36  Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752  
37                           Little Portugal, Trinity  43.647927 -79.419750  
41                       The Danforth West, Riverdale  43.679557 -79.352188  
42           Toronto Dominion Centre, Design Exchange  43.647177 -79.381576  
43       Brockton, Parkdale Village, Exhibition Place  43.636847 -79.428191  
47                     India Bazaar, The Beaches West  43.668999 -79.315572  
48                     Commerce Court, Victoria Hotel  43.648198 -79.379817  
54                                    Studio District  43.659526 -79.340923  
61                                      Lawrence Park  43.728020 -79.388790  
62                                           Roselawn  43.711695 -79.416936  
67                                   Davisville North  43.712751 -79.390197  
68    Forest Hill North & West, Forest Hill Road Park  43.696948 -79.411307  
69                      High Park, The Junction South  43.661608 -79.464763  
73                  North Toronto West, Lawrence Park  43.715383 -79.405678  
74                The Annex, North Midtown, Yorkville  43.672710 -79.405678  
75                             Parkdale, Roncesvalles  43.648960 -79.456325  
79                                         Davisville  43.704324 -79.388790  
80                     University of Toronto, Harbord  43.662696 -79.400049  
81                                 Runnymede, Swansea  43.651571 -79.484450  
83                        Moore Park, Summerhill East  43.689574 -79.383160  
84          Kensington Market, Chinatown, Grange Park  43.653206 -79.400049  
86  Summerhill West, Rathnelly, South Hill, Forest...  43.686412 -79.400049  
87  CN Tower, King and S

## Create Map of Toronto

In [59]:
address = 'Toronto, Toronto'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Downtown Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Downtown Toronto are 43.6534817, -79.3839347.


In [60]:
tor_latlong = [43.653225, -79.383186]

In [61]:
# create map of toronto using latitude and longitude values
tor_map = folium.Map(location=tor_latlong, zoom_start=10)

# add markers to map
for lat, lng, Borough, Neighborhood in zip(tor_data2['Latitude'], tor_data2['Longitude'], tor_data2['Borough'], tor_data2['Neighborhood']):
    label = '[], []'.format(Neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.75,
        parse_html=False).add_to(tor_map)

In [62]:
tor_map

## Pull in Four Square Data

In [63]:
CLIENT_ID = 'ES55HOGFTWDDGVGQDVLZL1LWGECN2QYQENAJSNKC4YAWNPDE' # your Foursquare ID
CLIENT_SECRET = 'DFZHSPCUFN5II3CM5VJVGZOV5UL5GETSPMNFGRGJ3GQUSTJE' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ES55HOGFTWDDGVGQDVLZL1LWGECN2QYQENAJSNKC4YAWNPDE
CLIENT_SECRET:DFZHSPCUFN5II3CM5VJVGZOV5UL5GETSPMNFGRGJ3GQUSTJE


## Only Look for Restaurants Category Type took a while to figure out

In [52]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

In [53]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?=&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
           radius, 
            LIMIT,
        "4d4b7105d754a06374d81259") #Food only category ID
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

In [79]:
toronto_venues = getNearbyVenues(names=tor_data2['Neighborhood'],
                                   latitudes=tor_data2['Latitude'],
                                   longitudes=tor_data2['Longitude']
                                  )

Regent Park, Harbourfront
Queen's Park, Ontario Provincial Government
Garden District, Ryerson
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
The Danforth West, Riverdale
Toronto Dominion Centre, Design Exchange
Brockton, Parkdale Village, Exhibition Place
India Bazaar, The Beaches West
Commerce Court, Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North & West, Forest Hill Road Park
High Park, The Junction South
North Toronto West, Lawrence Park
The Annex, North Midtown, Yorkville
Parkdale, Roncesvalles
Davisville
University of Toronto, Harbord
Runnymede, Swansea
Moore Park, Summerhill East
Kensington Market, Chinatown, Grange Park
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
R

## After pulling in venues look at shape and Count

In [80]:
print(toronto_venues.shape)
toronto_venues.head()

(1370, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Regent Park, Harbourfront               43.65426              -79.360636   
1  Regent Park, Harbourfront               43.65426              -79.360636   
2  Regent Park, Harbourfront               43.65426              -79.360636   
3  Regent Park, Harbourfront               43.65426              -79.360636   
4  Regent Park, Harbourfront               43.65426              -79.360636   

                        Venue  Venue Latitude  Venue Longitude  \
0              Impact Kitchen       43.656369       -79.356980   
1          Morning Glory Cafe       43.653947       -79.361149   
2      Figs Breakfast & Lunch       43.655675       -79.364503   
3         Brick Street Bakery       43.650574       -79.359539   
4  Cluny Bistro & Boulangerie       43.650565       -79.357843   

      Venue Category  
0         Restaurant  
1     Breakfast Spot  
2     Breakfast Spot  
3             Bakery  
4  French Restaurant

In [39]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            52   
Brockton, Parkdale Village, Exhibition Place                           15   
Business reply mail Processing Centre, South Ce...                      5   
CN Tower, King and Spadina, Railway Lands, Harb...                      2   
Central Bay Street                                                     67   
Christie                                                                7   
Church and Wellesley                                                   66   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             30   
Davisville North                                                        4   
Dufferin, Dovercourt Village                                            8   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                               98   
Harbourfront East, Union Station, Toronto Islands                      80   
High Park, The Junction South                                          15   
India Bazaar, The Beaches West                                         12   
Kensington Market, Chinatown, Grange Park                              55   
Lawrence Park                                                           1   
Little Portugal, Trinity                                               42   
Moore Park, Summerhill East                                             2   
North Toronto West, Lawrence Park                                       9   
Parkdale, Roncesvalles                                                  8   
Queen's Park, Ontario Provincial Government                            27   
Regent Park, Harbourfront                                              23   
Richmond, Adelaide, King                                               92   
Rosedale                                                                1   
Runnymede, Swansea                                                     25   
St. James Town                                                         75   
St. James Town, Cabbagetown                                            28   
Stn A PO Boxes                                                         99   
Studio District                                                        25   
Summerhill West, Rathnelly, South Hill, Forest ...                      9   
The Annex, North Midtown, Yorkville                                    14   
The Beaches                                                             3   
The Danforth West, Riverdale                                           38   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         29   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             52   
Brockton, Parkdale Village, Exhibition Place                            15   
Business reply mail Processing Centre, South Ce...                       5   
CN Tower, King and Spadina, Railway Lands, Harb...                       2   
Central Bay Street                                                      67   
Christie                                                                 7   
Church and Wellesley                                                    66   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              30   
Davisville North                                                         4   
Dufferin, Dovercourt Village       

In [81]:
print('Unique Categories:', format(len(toronto_venues['Venue Category'].unique())))

Unique Categories: 89


In [82]:
toronto_venues.dtypes

Neighborhood               object
Neighborhood Latitude     float64
Neighborhood Longitude    float64
Venue                      object
Venue Latitude            float64
Venue Longitude           float64
Venue Category             object
dtype: object

In [42]:
toronto_venues

Neighborhood  \
0                             Regent Park, Harbourfront   
1                             Regent Park, Harbourfront   
2                             Regent Park, Harbourfront   
3                             Regent Park, Harbourfront   
4                             Regent Park, Harbourfront   
5                             Regent Park, Harbourfront   
6                             Regent Park, Harbourfront   
7                             Regent Park, Harbourfront   
8                             Regent Park, Harbourfront   
9                             Regent Park, Harbourfront   
10                            Regent Park, Harbourfront   
11                            Regent Park, Harbourfront   
12                            Regent Park, Harbourfront   
13                            Regent Park, Harbourfront   
14                            Regent Park, Harbourfront   
15                            Regent Park, Harbourfront   
16                            Regent Park, Harbourfront   
17                            Regent Park, Harbourfront   
18                            Regent Park, Harbourfront   
19                            Regent Park, Harbourfront   
20                            Regent Park, Harbourfront   
21                            Regent Park, Harbourfront   
22                            Regent Park, Harbourfront   
23          Queen's Park, Ontario Provincial Government   
24          Queen's Park, Ontario Provincial Government   
25          Queen's Park, Ontario Provincial Government   
26          Queen's Park, Ontario Provincial Government   
27          Queen's Park, Ontario Provincial Government   
28          Queen's Park, Ontario Provincial Government   
29          Queen's Park, Ontario Provincial Government   
30          Queen's Park, Ontario Provincial Government   
31          Queen's Park, Ontario Provincial Government   
32          Queen's Park, Ontario Provincial Government   
33          Queen's Park, Ontario Provincial Government   
34          Queen's Park, Ontario Provincial Government   
35          Queen's Park, Ontario Provincial Government   
36          Queen's Park, Ontario Provincial Government   
37          Queen's Park, Ontario Provincial Government   
38          Queen's Park, Ontario Provincial Government   
39          Queen's Park, Ontario Provincial Government   
40          Queen's Park, Ontario Provincial Government   
41          Queen's Park, Ontario Provincial Government   
42          Queen's Park, Ontario Provincial Government   
43          Queen's Park, Ontario Provincial Government   
44          Queen's Park, Ontario Provincial Government   
45          Queen's Park, Ontario Provincial Government   
46          Queen's Park, Ontario Provincial Government   
47          Queen's Park, Ontario Provincial Government   
48          Queen's Park, Ontario Provincial Government   
49          Queen's Park, Ontario Provincial Government   
50                             Garden District, Ryerson   
51                             Garden District, Ryerson   
52                             Garden District, Ryerson   
53                             Garden District, Ryerson   
54                             Garden District, Ryerson   
55                             Garden District, Ryerson   
56                             Garden District, Ryerson   
57                             Garden District, Ryerson   
58                             Garden District, Ryerson   
59                             Garden District, Ryerson   
60                             Garden District, Ryerson   
61                             Garden District, Ryerson   
62                             Garden District, Ryerson   
63                             Garden District, Ryerson   
64                             Garden District, Ryerson   
65                             Garden District, Ryerson   
66                             Garden District, Ryerson   
67                             

## Pull in One Hot encoding

In [83]:
# one hot encoding
tor_hot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
tor_hot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
cols=list(tor_hot.columns.values)
cols.pop(cols.index('Neighborhood'))
tor_hot=tor_hot[['Neighborhood']+cols]

# rename Neighborhood for Neighbourhood so that future merge works
tor_hot

Neighborhood  Afghan Restaurant  \
0                             Regent Park, Harbourfront                  0   
1                             Regent Park, Harbourfront                  0   
2                             Regent Park, Harbourfront                  0   
3                             Regent Park, Harbourfront                  0   
4                             Regent Park, Harbourfront                  0   
5                             Regent Park, Harbourfront                  0   
6                             Regent Park, Harbourfront                  0   
7                             Regent Park, Harbourfront                  0   
8                             Regent Park, Harbourfront                  0   
9                             Regent Park, Harbourfront                  0   
10                            Regent Park, Harbourfront                  0   
11                            Regent Park, Harbourfront                  0   
12                            Regent Park, Harbourfront                  0   
13                            Regent Park, Harbourfront                  0   
14                            Regent Park, Harbourfront                  0   
15                            Regent Park, Harbourfront                  0   
16                            Regent Park, Harbourfront                  0   
17                            Regent Park, Harbourfront                  0   
18                            Regent Park, Harbourfront                  0   
19                            Regent Park, Harbourfront                  0   
20                            Regent Park, Harbourfront                  0   
21                            Regent Park, Harbourfront                  0   
22                            Regent Park, Harbourfront                  0   
23          Queen's Park, Ontario Provincial Government                  0   
24          Queen's Park, Ontario Provincial Government                  0   
25          Queen's Park, Ontario Provincial Government                  0   
26          Queen's Park, Ontario Provincial Government                  0   
27          Queen's Park, Ontario Provincial Government                  0   
28          Queen's Park, Ontario Provincial Government                  0   
29          Queen's Park, Ontario Provincial Government                  0   
30          Queen's Park, Ontario Provincial Government                  0   
31          Queen's Park, Ontario Provincial Government                  0   
32          Queen's Park, Ontario Provincial Government                  0   
33          Queen's Park, Ontario Provincial Government                  0   
34          Queen's Park, Ontario Provincial Government                  0   
35          Queen's Park, Ontario Provincial Government                  0   
36          Queen's Park, Ontario Provincial Government                  0   
37          Queen's Park, Ontario Provincial Government                  0   
38          Queen's Park, Ontario Provincial Government                  0   
39          Queen's Park, Ontario Provincial Government                  0   
40          Queen's Park, Ontario Provincial Government                  0   
41          Queen's Park, Ontario Provincial Government                  0   
42          Queen's Park, Ontario Provincial Government                  0   
43          Queen's Park, Ontario Provincial Government                  0   
44          Queen's Park, Ontario Provincial Government                  0   
45          Queen's Park, Ontario Provincial Government                  0   
46          Queen's Park, Ontario Provincial Government                  0   
47          Queen's Park, Ontario Provincial Government                  0   
48          Queen's Park, Ontario Provincial Government                  0   
49          Queen's Park, Ontario Provincial Government                  0   
50                             Garden District, Ryerson          

In [84]:
tor_hot.shape

(1370, 90)

## Pull in mean 

In [85]:
tor_group = tor_hot.groupby('Neighborhood').mean().reset_index()
tor_group


Neighborhood  Afghan Restaurant  \
0                                         Berczy Park           0.000000   
1        Brockton, Parkdale Village, Exhibition Place           0.000000   
2   Business reply mail Processing Centre, South C...           0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
4                                  Central Bay Street           0.000000   
5                                            Christie           0.000000   
6                                Church and Wellesley           0.015152   
7                      Commerce Court, Victoria Hotel           0.000000   
8                                          Davisville           0.000000   
9                                    Davisville North           0.000000   
10                       Dufferin, Dovercourt Village           0.000000   
11             First Canadian Place, Underground city           0.000000   
12    Forest Hill North & West, Forest Hill Road Park           0.000000   
13                           Garden District, Ryerson           0.000000   
14  Harbourfront East, Union Station, Toronto Islands           0.000000   
15                      High Park, The Junction South           0.000000   
16                     India Bazaar, The Beaches West           0.000000   
17          Kensington Market, Chinatown, Grange Park           0.000000   
18                                      Lawrence Park           0.000000   
19                           Little Portugal, Trinity           0.000000   
20                        Moore Park, Summerhill East           0.000000   
21                  North Toronto West, Lawrence Park           0.000000   
22                             Parkdale, Roncesvalles           0.000000   
23        Queen's Park, Ontario Provincial Government           0.000000   
24                          Regent Park, Harbourfront           0.000000   
25                           Richmond, Adelaide, King           0.000000   
26                                           Rosedale           0.000000   
27                                 Runnymede, Swansea           0.000000   
28                                     St. James Town           0.000000   
29                        St. James Town, Cabbagetown           0.000000   
30                                     Stn A PO Boxes           0.000000   
31                                    Studio District           0.000000   
32  Summerhill West, Rathnelly, South Hill, Forest...           0.000000   
33                The Annex, North Midtown, Yorkville           0.000000   
34                                        The Beaches           0.000000   
35                       The Danforth West, Riverdale           0.000000   
36           Toronto Dominion Centre, Design Exchange           0.000000   
37                     University of Toronto, Harbord           0.000000   

    American Restaurant  Arepa Restaurant  Argentinian Restaurant  \
0              0.019231          0.000000                 0.00000   
1              0.000000          0.000000                 0.00000   
2              0.000000          0.000000                 0.00000   
3              0.500000          0.000000                 0.00000   
4              0.000000          0.000000                 0.00000   
5              0.000000          0.000000                 0.00000   
6              0.015152          0.000000                 0.00000   
7              0.050000          0.000000                 0.00000   
8              0.066667          0.000000                 0.00000   
9              0.000000          0.000000                 0.00000   
10             0.000000          0.000000                 0.00000   
11             0.060000          0.000000                 0.00000   
12             0.000000          0.000000                 0.00000   
13             0.010204          0.000000                 0.00000   
14             0.012500          0.000000

In [86]:
tor_group.shape

(38, 90)

## Pull in frequency

In [87]:
num_top_venues = 10

for hood in tor_group['Neighborhood']:
    print("----"+hood+"----")
    temp = tor_group[tor_group['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Berczy Park----
                 venue  freq
0       Sandwich Place  0.08
1               Bakery  0.08
2   Italian Restaurant  0.06
3           Restaurant  0.06
4     Sushi Restaurant  0.06
5                 Café  0.06
6     Greek Restaurant  0.04
7    French Restaurant  0.04
8   Seafood Restaurant  0.04
9  Moroccan Restaurant  0.04


----Brockton, Parkdale Village, Exhibition Place----
                   venue  freq
0                   Café  0.27
1                 Bakery  0.13
2         Sandwich Place  0.13
3         Breakfast Spot  0.13
4     Italian Restaurant  0.07
5             Restaurant  0.07
6          Burrito Place  0.07
7  Vietnamese Restaurant  0.07
8    Japanese Restaurant  0.07
9     Mac & Cheese Joint  0.00


----Business reply mail Processing Centre, South Central Letter Processing Plant Toronto----
                     venue  freq
0     Fast Food Restaurant   0.4
1               Restaurant   0.2
2              Pizza Place   0.2
3            Burrito Place   0.2
4    

In [89]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [90]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neigh_venues_sort = pd.DataFrame(columns=columns)
neigh_venues_sort['Neighborhood'] = tor_group['Neighborhood']

for ind in np.arange(tor_group.shape[0]):
    neigh_venues_sort.iloc[ind, 1:] = return_most_common_venues(tor_group.iloc[ind, :], num_top_venues)

neigh_venues_sort

Neighborhood 1st Most Common Venue  \
0                                         Berczy Park                Bakery   
1        Brockton, Parkdale Village, Exhibition Place                  Café   
2   Business reply mail Processing Centre, South C...  Fast Food Restaurant   
3   CN Tower, King and Spadina, Railway Lands, Har...   American Restaurant   
4                                  Central Bay Street                  Café   
5                                            Christie                  Café   
6                                Church and Wellesley      Sushi Restaurant   
7                      Commerce Court, Victoria Hotel                  Café   
8                                          Davisville           Pizza Place   
9                                    Davisville North        Breakfast Spot   
10                       Dufferin, Dovercourt Village                Bakery   
11             First Canadian Place, Underground city                  Café   
12    Forest Hill North & West, Forest Hill Road Park            Restaurant   
13                           Garden District, Ryerson                  Café   
14  Harbourfront East, Union Station, Toronto Islands            Restaurant   
15                      High Park, The Junction South    Mexican Restaurant   
16                     India Bazaar, The Beaches West           Pizza Place   
17          Kensington Market, Chinatown, Grange Park                  Café   
18                                      Lawrence Park    Dim Sum Restaurant   
19                           Little Portugal, Trinity      Asian Restaurant   
20                        Moore Park, Summerhill East            Restaurant   
21                  North Toronto West, Lawrence Park    Mexican Restaurant   
22                             Parkdale, Roncesvalles        Breakfast Spot   
23        Queen's Park, Ontario Provincial Government      Sushi Restaurant   
24                          Regent Park, Harbourfront                  Café   
25                           Richmond, Adelaide, King                  Café   
26                                           Rosedale   Japanese Restaurant   
27                                 Runnymede, Swansea           Pizza Place   
28                                     St. James Town            Restaurant   
29                        St. James Town, Cabbagetown           Pizza Place   
30                                     Stn A PO Boxes        Sandwich Place   
31                                    Studio District                  Café   
32  Summerhill West, Rathnelly, South Hill, Forest...   Fried Chicken Joint   
33                The Annex, North Midtown, Yorkville                  Café   
34                                        The Beaches           Pizza Place   
35                       The Danforth West, Riverdale      Greek Restaurant   
36           Toronto Dominion Centre, Design Exchange            Restaurant   
37                     University of Toronto, Harbord                  Café   

            2nd Most Common Venue          3rd Most Common Venue  \
0                  Sandwich Place                           Café   
1                          Bakery                 Breakfast Spot   
2                     Pizza Place                     Restaurant   
3                Tapas Restaurant                    Wings Joint   
4              Italian Restaurant                 Sandwich Place   
5                           Diner                     Restaurant   
6             Japanese Restaurant                    Pizza Place   
7                      Restaurant             Italian Restaurant   
8                            Café                 Sandwich Place   
9                Asian Restaurant                 Sandwich Place   
10                    Pizza Place          Portuguese Restaurant   
11                     Restaurant            American Restaurant   
12              French Restaurant               Sushi Restaurant   
13     

## Calculate KMeans clusters

In [91]:
# set number of clusters
k = 5

tor_cluster = tor_group.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=k, random_state=0).fit(tor_cluster)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([0, 0, 0, 2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 3, 0,
       0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [94]:
tor_data3 = tor_data2

# add clustering labels
tor_data3['Cluster Labels'] = kmeans.labels_

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
tor_data3 = tor_data3.join(neigh_venues_sort.set_index('Neighborhood'), on='Neighborhood')

tor_data3# check the last columns!

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


Postal Code           Borough  \
2          M5A  Downtown Toronto   
4          M7A  Downtown Toronto   
9          M5B  Downtown Toronto   
15         M5C  Downtown Toronto   
19         M4E      East Toronto   
20         M5E  Downtown Toronto   
24         M5G  Downtown Toronto   
25         M6G  Downtown Toronto   
30         M5H  Downtown Toronto   
31         M6H      West Toronto   
36         M5J  Downtown Toronto   
37         M6J      West Toronto   
41         M4K      East Toronto   
42         M5K  Downtown Toronto   
43         M6K      West Toronto   
47         M4L      East Toronto   
48         M5L  Downtown Toronto   
54         M4M      East Toronto   
61         M4N   Central Toronto   
62         M5N   Central Toronto   
67         M4P   Central Toronto   
68         M5P   Central Toronto   
69         M6P      West Toronto   
73         M4R   Central Toronto   
74         M5R   Central Toronto   
75         M6R      West Toronto   
79         M4S   Central Toronto   
80         M5S  Downtown Toronto   
81         M6S      West Toronto   
83         M4T   Central Toronto   
84         M5T  Downtown Toronto   
86         M4V   Central Toronto   
87         M5V  Downtown Toronto   
91         M4W  Downtown Toronto   
92         M5W  Downtown Toronto   
96         M4X  Downtown Toronto   
97         M5X  Downtown Toronto   
99         M4Y  Downtown Toronto   

                                         Neighborhood   Latitude  Longitude  \
2                           Regent Park, Harbourfront  43.654260 -79.360636   
4         Queen's Park, Ontario Provincial Government  43.662301 -79.389494   
9                            Garden District, Ryerson  43.657162 -79.378937   
15                                     St. James Town  43.651494 -79.375418   
19                                        The Beaches  43.676357 -79.293031   
20                                        Berczy Park  43.644771 -79.373306   
24                                 Central Bay Street  43.657952 -79.387383   
25                                           Christie  43.669542 -79.422564   
30                           Richmond, Adelaide, King  43.650571 -79.384568   
31                       Dufferin, Dovercourt Village  43.669005 -79.442259   
36  Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752   
37                           Little Portugal, Trinity  43.647927 -79.419750   
41                       The Danforth West, Riverdale  43.679557 -79.352188   
42           Toronto Dominion Centre, Design Exchange  43.647177 -79.381576   
43       Brockton, Parkdale Village, Exhibition Place  43.636847 -79.428191   
47                     India Bazaar, The Beaches West  43.668999 -79.315572   
48                     Commerce Court, Victoria Hotel  43.648198 -79.379817   
54                                    Studio District  43.659526 -79.340923   
61                                      Lawrence Park  43.728020 -79.388790   
62                                           Roselawn  43.711695 -79.416936   
67                                   Davisville North  43.712751 -79.390197   
68    Forest Hill North & West, Forest Hill Road Park  43.696948 -79.411307   
69                      High Park, The Junction South  43.661608 -79.464763   
73                  North Toronto West, Lawrence Park  43.715383 -79.405678   
74                The Annex, North Midtown, Yorkville  43.672710 -79.405678   
75                             Parkdale, Roncesvalles  43.648960 -79.456325   
79                                         Davisville  43.704324 -79.388790   
80                     University of Toronto, Harbord  43.662696 -79.400049   
81                                 Runnymede, Swansea  43.651571 -79.484450   
83                        Moore Park, Summerhill East  43.689574 -79.383160   
84          Kensington Market, Chinatown, Grange Park  43.653206 -79.400049   
86  Summerhill West, Rathnelly, South Hill, Forest...  43.686412 -79.4

In [95]:
tor_data3.loc[tor_data3['Cluster Labels'] == 0, tor_data3.columns[[1] + list(range(5, tor_data3.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
2   Downtown Toronto               0                  Café   
4   Downtown Toronto               0      Sushi Restaurant   
9   Downtown Toronto               0                  Café   
19      East Toronto               0           Pizza Place   
20  Downtown Toronto               0                Bakery   
24  Downtown Toronto               0                  Café   
25  Downtown Toronto               0                  Café   
30  Downtown Toronto               0                  Café   
31      West Toronto               0                Bakery   
36  Downtown Toronto               0            Restaurant   
37      West Toronto               0      Asian Restaurant   
41      East Toronto               0      Greek Restaurant   
42  Downtown Toronto               0            Restaurant   
43      West Toronto               0                  Café   
47      East Toronto               0           Pizza Place   
48  Downtown Toronto               0                  Café   
54      East Toronto               0                  Café   
62   Central Toronto               0                   NaN   
68   Central Toronto               0            Restaurant   
69      West Toronto               0    Mexican Restaurant   
73   Central Toronto               0    Mexican Restaurant   
74   Central Toronto               0                  Café   
75      West Toronto               0        Breakfast Spot   
80  Downtown Toronto               0                  Café   
81      West Toronto               0           Pizza Place   
83   Central Toronto               0            Restaurant   
84  Downtown Toronto               0                  Café   
86   Central Toronto               0   Fried Chicken Joint   
87  Downtown Toronto               0   American Restaurant   
91  Downtown Toronto               0   Japanese Restaurant   
92  Downtown Toronto               0        Sandwich Place   
96  Downtown Toronto               0           Pizza Place   
97  Downtown Toronto               0                  Café   
99  Downtown Toronto               0      Sushi Restaurant   

            2nd Most Common Venue          3rd Most Common Venue  \
2                          Bakery                     Restaurant   
4                    Burger Joint                  Burrito Place   
9                      Restaurant                    Pizza Place   
19               Asian Restaurant                   Burger Joint   
20                 Sandwich Place                           Café   
24             Italian Restaurant                 Sandwich Place   
25                          Diner                     Restaurant   
30                     Restaurant                 Sandwich Place   
31                    Pizza Place          Portuguese Restaurant   
36                           Café           Fast Food Restaurant   
37                     Restaurant  Vegetarian / Vegan Restaurant   
41               Sushi Restaurant             Italian Restaurant   
42                           Café                 Sandwich Place   
43                         Bakery                 Breakfast Spot   
47           Fast Food Restaurant                 Sandwich Place   
48                     Restaurant             Italian Restaurant   
54                    Pizza Place                         Bakery   
62                            NaN                            NaN   
68              French Restaurant               Sushi Restaurant   
69                Thai Restaurant                         Bakery   
73                          Diner             Chinese Restaurant   
74                 Sandwich Place  Vegetarian / Vegan Restaurant   
75             Italian Restaurant                  Deli / Bodega   
80                 Sandwich Place                     Restaurant   
81                           Café               Sushi Restaurant   
83             Italian Restaurant                    Wings Joint   
84  Ve

In [96]:
tor_data3.loc[tor_data3['Cluster Labels'] == 1, tor_data3.columns[[1] + list(range(5, tor_data3.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
61  Central Toronto               1    Dim Sum Restaurant   

   2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
61           Wings Joint  Gluten-free Restaurant         Deli / Bodega   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
61                 Diner      Doner Restaurant            Donut Shop   

   8th Most Common Venue        9th Most Common Venue 10th Most Common Venue  
61   Dumpling Restaurant  Eastern European Restaurant    Empanada Restaurant

In [97]:
tor_data3.loc[tor_data3['Cluster Labels'] == 2, tor_data3.columns[[1] + list(range(5, tor_data3.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
15  Downtown Toronto               2            Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
15                  Café    Italian Restaurant      Sushi Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
15                 Diner        Breakfast Spot             Gastropub   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
15                Bakery   American Restaurant              BBQ Joint

In [98]:
tor_data3.loc[tor_data3['Cluster Labels'] == 3, tor_data3.columns[[1] + list(range(5, tor_data3.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
67  Central Toronto               3        Breakfast Spot   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
67      Asian Restaurant        Sandwich Place           Pizza Place   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
67            Food Truck     French Restaurant         Deli / Bodega   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
67    Dim Sum Restaurant                 Diner       Doner Restaurant

In [100]:
tor_data3.loc[tor_data3['Cluster Labels'] == 4, tor_data3.columns[[1] + list(range(5, tor_data3.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
79  Central Toronto               4           Pizza Place   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
79                  Café        Sandwich Place   American Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
79    Italian Restaurant      Sushi Restaurant    Seafood Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
79   Fried Chicken Joint     Indian Restaurant    Japanese Restaurant

## Graph KMeans clusters

In [172]:
# create map
map_clusters = folium.Map(location=tor_latlong, zoom_start=10)

# set color scheme for the clusters
x = np.arange(k)
ys = [i+x+(i*x)**2 for i in range(k)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(tor_data3['Latitude'], tor_data3['Longitude'], tor_data3['Neighborhood'], tor_data3['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Use Category ID and Pull in only Italian Restaraunts only

In [ ]:
plt.savefig('map_clusters.jpg', dpi=300)

In [102]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?=&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
           radius, 
            LIMIT,
        "4bf58dd8d48988d110941735") #Food only category ID
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

In [103]:
toronto_venues = getNearbyVenues(names=tor_data2['Neighborhood'],
                                   latitudes=tor_data2['Latitude'],
                                   longitudes=tor_data2['Longitude']
                                  )

Regent Park, Harbourfront
Queen's Park, Ontario Provincial Government
Garden District, Ryerson
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
The Danforth West, Riverdale
Toronto Dominion Centre, Design Exchange
Brockton, Parkdale Village, Exhibition Place
India Bazaar, The Beaches West
Commerce Court, Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North & West, Forest Hill Road Park
High Park, The Junction South
North Toronto West, Lawrence Park
The Annex, North Midtown, Yorkville
Parkdale, Roncesvalles
Davisville
University of Toronto, Harbord
Runnymede, Swansea
Moore Park, Summerhill East
Kensington Market, Chinatown, Grange Park
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
R

In [104]:
print(toronto_venues.shape)
toronto_venues.head()

(202, 7)


Neighborhood  Neighborhood Latitude  \
0                    Regent Park, Harbourfront              43.654260   
1                    Regent Park, Harbourfront              43.654260   
2                    Regent Park, Harbourfront              43.654260   
3  Queen's Park, Ontario Provincial Government              43.662301   
4  Queen's Park, Ontario Provincial Government              43.662301   

   Neighborhood Longitude        Venue  Venue Latitude  Venue Longitude  \
0              -79.360636       Archeo       43.650667       -79.359431   
1              -79.360636  Caffe Furbo       43.649970       -79.358849   
2              -79.360636        Basso       43.655532       -79.365071   
3              -79.389494     Mercatto       43.660391       -79.387664   
4              -79.389494        Tosto       43.661198       -79.386414   

       Venue Category  
0  Italian Restaurant  
1                Café  
2  Italian Restaurant  
3  Italian Restaurant  
4  Italian Restaurant

## Count Italian Restaurants

In [105]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                               
Berczy Park                                                            8   
Brockton, Parkdale Village, Exhibition Place                           1   
Central Bay Street                                                    16   
Christie                                                               2   
Church and Wellesley                                                   5   
Commerce Court, Victoria Hotel                                        26   
Davisville                                                             3   
First Canadian Place, Underground city                                20   
Garden District, Ryerson                                              11   
Harbourfront East, Union Station, Toronto Islands                      5   
High Park, The Junction South                                          1   
India Bazaar, The Beaches West                                         1   
Kensington Market, Chinatown, Grange Park                              4   
Little Portugal, Trinity                                               5   
North Toronto West, Lawrence Park                                      1   
Parkdale, Roncesvalles                                                 1   
Queen's Park, Ontario Provincial Government                            3   
Regent Park, Harbourfront                                              3   
Richmond, Adelaide, King                                              13   
Runnymede, Swansea                                                     2   
St. James Town                                                        20   
St. James Town, Cabbagetown                                            2   
Stn A PO Boxes                                                        15   
Studio District                                                        2   
The Danforth West, Riverdale                                           5   
Toronto Dominion Centre, Design Exchange                              24   
University of Toronto, Harbord                                         3   

                                                   Neighborhood Longitude  \
Neighborhood                                                                
Berczy Park                                                             8   
Brockton, Parkdale Village, Exhibition Place                            1   
Central Bay Street                                                     16   
Christie                                                                2   
Church and Wellesley                                                    5   
Commerce Court, Victoria Hotel                                         26   
Davisville                                                              3   
First Canadian Place, Underground city                                 20   
Garden District, Ryerson                                               11   
Harbourfront East, Union Station, Toronto Islands                       5   
High Park, The Junction South                                           1   
India Bazaar, The Beaches West                                          1   
Kensington Market, Chinatown, Grange Park                               4   
Little Portugal, Trinity                                                5   
North Toronto West, Lawrence Park                                       1   
Parkdale, Roncesvalles                                                  1   
Queen's Park, Ontario Provincial Government                             3   
Regent Park, Harbourfront                                               3   
Richmond, Adelaide, King                                               13   
Runnymede, Swansea                                                      2   
St. James Town                                                         20   
St. James Town, Cabbagetown                                             2  

In [106]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 12 uniques categories.


In [111]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                    Regent Park, Harbourfront              43.654260   
1                    Regent Park, Harbourfront              43.654260   
2                    Regent Park, Harbourfront              43.654260   
3  Queen's Park, Ontario Provincial Government              43.662301   
4  Queen's Park, Ontario Provincial Government              43.662301   

   Neighborhood Longitude        Venue  Venue Latitude  Venue Longitude  \
0              -79.360636       Archeo       43.650667       -79.359431   
1              -79.360636  Caffe Furbo       43.649970       -79.358849   
2              -79.360636        Basso       43.655532       -79.365071   
3              -79.389494     Mercatto       43.660391       -79.387664   
4              -79.389494        Tosto       43.661198       -79.386414   

       Venue Category  
0  Italian Restaurant  
1                Café  
2  Italian Restaurant  
3  Italian Restaurant  
4  Italian Restaurant

## Join italian restaurants to get mapping info

## Map Italian Restaurants

In [112]:
# create map of toronto using latitude and longitude values
tor_map = folium.Map(location=tor_latlong, zoom_start=10)

# add markers to map
for lat, lng, Neighborhood in zip(toronto_venues['Neighborhood Latitude'], toronto_venues['Neighborhood Longitude'], toronto_venues['Neighborhood']):
    label = '[], []'.format(Neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.75,
        parse_html=False).add_to(tor_map)

In [113]:
tor_map

In [171]:
plt.savefig('tor_map.jpg', dpi=300)

<Figure size 432x288 with 0 Axes>

## Grab New York Data from file in Lab

In [114]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


## Grab as JSON

In [115]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [116]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

## Look at Features of 0

In [117]:
neighborhoods_data = newyork_data['features']

In [118]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

## Define dataframe

In [119]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [120]:
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

## Convert into DF

In [121]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [122]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [123]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


## Pull in NYC Coordinates and MAP 

In [124]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [125]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Pull in Manhattan Code Only

In [126]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data

Borough         Neighborhood   Latitude  Longitude
0   Manhattan          Marble Hill  40.876551 -73.910660
1   Manhattan            Chinatown  40.715618 -73.994279
2   Manhattan   Washington Heights  40.851903 -73.936900
3   Manhattan               Inwood  40.867684 -73.921210
4   Manhattan     Hamilton Heights  40.823604 -73.949688
5   Manhattan       Manhattanville  40.816934 -73.957385
6   Manhattan       Central Harlem  40.815976 -73.943211
7   Manhattan          East Harlem  40.792249 -73.944182
8   Manhattan      Upper East Side  40.775639 -73.960508
9   Manhattan            Yorkville  40.775930 -73.947118
10  Manhattan           Lenox Hill  40.768113 -73.958860
11  Manhattan     Roosevelt Island  40.762160 -73.949168
12  Manhattan      Upper West Side  40.787658 -73.977059
13  Manhattan       Lincoln Square  40.773529 -73.985338
14  Manhattan              Clinton  40.759101 -73.996119
15  Manhattan              Midtown  40.754691 -73.981669
16  Manhattan          Murray Hill  40.748303 -73.978332
17  Manhattan              Chelsea  40.744035 -74.003116
18  Manhattan    Greenwich Village  40.726933 -73.999914
19  Manhattan         East Village  40.727847 -73.982226
20  Manhattan      Lower East Side  40.717807 -73.980890
21  Manhattan              Tribeca  40.721522 -74.010683
22  Manhattan         Little Italy  40.719324 -73.997305
23  Manhattan                 Soho  40.722184 -74.000657
24  Manhattan         West Village  40.734434 -74.006180
25  Manhattan     Manhattan Valley  40.797307 -73.964286
26  Manhattan  Morningside Heights  40.808000 -73.963896
27  Manhattan             Gramercy  40.737210 -73.981376
28  Manhattan    Battery Park City  40.711932 -74.016869
29  Manhattan   Financial District  40.707107 -74.010665
30  Manhattan        Carnegie Hill  40.782683 -73.953256
31  Manhattan                 Noho  40.723259 -73.988434
32  Manhattan         Civic Center  40.715229 -74.005415
33  Manhattan        Midtown South  40.748510 -73.988713
34  Manhattan         Sutton Place  40.760280 -73.963556
35  Manhattan           Turtle Bay  40.752042 -73.967708
36  Manhattan           Tudor City  40.746917 -73.971219
37  Manhattan      Stuyvesant Town  40.731000 -73.974052
38  Manhattan             Flatiron  40.739673 -73.990947
39  Manhattan         Hudson Yards  40.756658 -74.000111

In [127]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


In [128]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

## Grab Restaraunts category from FourSquare

In [170]:
plt.savefig('map_manhattan.jpg', dpi=300)

<Figure size 432x288 with 0 Axes>

In [100]:
CLIENT_ID = 'ES55HOGFTWDDGVGQDVLZL1LWGECN2QYQENAJSNKC4YAWNPDE' # your Foursquare ID
CLIENT_SECRET = 'DFZHSPCUFN5II3CM5VJVGZOV5UL5GETSPMNFGRGJ3GQUSTJE' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ES55HOGFTWDDGVGQDVLZL1LWGECN2QYQENAJSNKC4YAWNPDE
CLIENT_SECRET:DFZHSPCUFN5II3CM5VJVGZOV5UL5GETSPMNFGRGJ3GQUSTJE


In [129]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?=&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
           radius, 
            LIMIT,
        "4d4b7105d754a06374d81259") #Food only category ID
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

In [130]:
# type your answer here

manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


## Grab shape and count

In [131]:
print(manhattan_venues.shape)
manhattan_venues.head()

(2787, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551               -73.91066   
1  Marble Hill              40.876551               -73.91066   
2  Marble Hill              40.876551               -73.91066   
3  Marble Hill              40.876551               -73.91066   
4  Marble Hill              40.876551               -73.91066   

                   Venue  Venue Latitude  Venue Longitude      Venue Category  
0               Arturo's       40.874412       -73.910271         Pizza Place  
1          Tibbett Diner       40.880404       -73.908937               Diner  
2                Dunkin'       40.877136       -73.906666          Donut Shop  
3  Land & Sea Restaurant       40.877885       -73.905873  Seafood Restaurant  
4                 Subway       40.874667       -73.909586      Sandwich Place

In [132]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       29                      29     29   
Carnegie Hill                           72                      72     72   
Central Harlem                          44                      44     44   
Chelsea                                 85                      85     85   
Chinatown                              100                     100    100   
Civic Center                            80                      80     80   
Clinton                                100                     100    100   
East Harlem                             51                      51     51   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                                99                      99     99   
Gramercy                                52                      52     52   
Greenwich Village                      100                     100    100   
Hamilton Heights                        59                      59     59   
Hudson Yards                            48                      48     48   
Inwood                                  49                      49     49   
Lenox Hill                             100                     100    100   
Lincoln Square                          52                      52     52   
Little Italy                           100                     100    100   
Lower East Side                         41                      41     41   
Manhattan Valley                        43                      43     43   
Manhattanville                          47                      47     47   
Marble Hill                             14                      14     14   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     40                      40     40   
Murray Hill                             80                      80     80   
Noho                                   100                     100    100   
Roosevelt Island                        12                      12     12   
Soho                                   100                     100    100   
Stuyvesant Town                          5                       5      5   
Sutton Place                            71                      71     71   
Tribeca                                 65                      65     65   
Tudor City                              82                      82     82   
Turtle Bay                              81                      81     81   
Upper East Side                         72                      72     72   
Upper West Side                         57                      57     57   
Washington Heights                      73                      73     73   
West Village                           100                     100    100   
Yorkville                               84                      84     84   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                29               29              29  
Carnegie Hill                    72               72              72  
Central Harlem                   44               44              44  
Chelsea                          85               85              85  
Chinatown                       100              100             100  
Civic Center                     80               80              80  
Clinton                         100              100             100  
East Harlem                      51               51              51  
East Village                    100              100             100  
Finan

In [133]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 126 uniques categories.


## Grab onehot caluclations

In [134]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Afghan Restaurant  African Restaurant  American Restaurant  \
0  Marble Hill                  0                   0                    0   
1  Marble Hill                  0                   0                    0   
2  Marble Hill                  0                   0                    0   
3  Marble Hill                  0                   0                    0   
4  Marble Hill                  0                   0                    0   

   Arepa Restaurant  Argentinian Restaurant  Asian Restaurant  \
0                 0                       0                 0   
1                 0                       0                 0   
2                 0                       0                 0   
3                 0                       0                 0   
4                 0                       0                 0   

   Australian Restaurant  Austrian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                      0                    0          0           0       0   
1                      0                    0          0           0       0   
2                      0                    0          0           0       0   
3                      0                    0          0           0       0   
4                      0                    0          0           0       0   

   Belgian Restaurant  Bistro  Brazilian Restaurant  Breakfast Spot  \
0                   0       0                     0               0   
1                   0       0                     0               0   
2                   0       0                     0               0   
3                   0       0                     0               0   
4                   0       0                     0               0   

   Burger Joint  Burrito Place  Cafeteria  Café  Cajun / Creole Restaurant  \
0             0              0          0     0                          0   
1             0              0          0     0                          0   
2             0              0          0     0                          0   
3             0              0          0     0                          0   
4             0              0          0     0                          0   

   Cambodian Restaurant  Cantonese Restaurant  Caribbean Restaurant  \
0                     0                     0                     0   
1                     0                     0                     0   
2                     0                     0                     0   
3                     0                     0                     0   
4                     0                     0                     0   

   Caucasian Restaurant  Cha Chaan Teng  Chinese Restaurant  Creperie  \
0                     0               0                   0         0   
1                     0               0                   0         0   
2                     0               0                   0         0   
3                     0               0                   0         0   
4                     0               0                   0         0   

   Cuban Restaurant  Czech Restaurant  Deli / Bodega  Dim Sum Restaurant  \
0                 0                 0              0                   0   
1                 0                 0              0                   0   
2                 0                 0              0                   0   
3                 0                 0              0                   0   
4                 0                 0              0                   0   

   Diner  Donut Shop  Dumpling Restaurant  Eastern European Restaurant  \
0      0           0                    0                            0   
1      1           0                    0                            0   
2      0           1                    0                            0   
3      0           0                    0                            0   
4      0           0                    0                            0  

In [135]:
manhattan_onehot.shape

(2787, 127)

In [136]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Afghan Restaurant  African Restaurant  \
0     Battery Park City               0.00            0.000000   
1         Carnegie Hill               0.00            0.000000   
2        Central Harlem               0.00            0.068182   
3               Chelsea               0.00            0.000000   
4             Chinatown               0.00            0.000000   
5          Civic Center               0.00            0.000000   
6               Clinton               0.00            0.000000   
7           East Harlem               0.00            0.000000   
8          East Village               0.00            0.000000   
9    Financial District               0.00            0.000000   
10             Flatiron               0.00            0.000000   
11             Gramercy               0.00            0.000000   
12    Greenwich Village               0.00            0.000000   
13     Hamilton Heights               0.00            0.000000   
14         Hudson Yards               0.00            0.000000   
15               Inwood               0.00            0.000000   
16           Lenox Hill               0.01            0.000000   
17       Lincoln Square               0.00            0.000000   
18         Little Italy               0.00            0.000000   
19      Lower East Side               0.00            0.000000   
20     Manhattan Valley               0.00            0.000000   
21       Manhattanville               0.00            0.000000   
22          Marble Hill               0.00            0.000000   
23              Midtown               0.00            0.000000   
24        Midtown South               0.00            0.000000   
25  Morningside Heights               0.00            0.000000   
26          Murray Hill               0.00            0.000000   
27                 Noho               0.00            0.000000   
28     Roosevelt Island               0.00            0.000000   
29                 Soho               0.00            0.000000   
30      Stuyvesant Town               0.00            0.000000   
31         Sutton Place               0.00            0.000000   
32              Tribeca               0.00            0.000000   
33           Tudor City               0.00            0.000000   
34           Turtle Bay               0.00            0.000000   
35      Upper East Side               0.00            0.000000   
36      Upper West Side               0.00            0.000000   
37   Washington Heights               0.00            0.000000   
38         West Village               0.00            0.000000   
39            Yorkville               0.00            0.000000   

    American Restaurant  Arepa Restaurant  Argentinian Restaurant  \
0              0.034483          0.000000                0.000000   
1              0.013889          0.000000                0.013889   
2              0.045455          0.000000                0.000000   
3              0.058824          0.011765                0.000000   
4              0.030000          0.000000                0.000000   
5              0.062500          0.000000                0.000000   
6              0.070000          0.000000                0.000000   
7              0.000000          0.000000                0.000000   
8              0.030000          0.010000                0.010000   
9              0.060000          0.000000                0.000000   
10             0.060606          0.000000                0.000000   
11             0.076923          0.000000                0.000000   
12             0.040000          0.000000                0.000000   
13             0.000000          0.000000                0.000000   
14             0.125000          0.000000                0.000000   
15             0.040816          0.000000                0.000000   
16             0.040000          0.000000                0.000000   
17             0.096154          0.000000                0.000

In [111]:
manhattan_grouped.shape

(40, 125)

## Look for top restaurant venues

In [137]:
num_top_venues = 10

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
                venue  freq
0         Pizza Place  0.14
1  Chinese Restaurant  0.14
2      Sandwich Place  0.10
3          Food Court  0.07
4        Burger Joint  0.07
5          Donut Shop  0.07
6              Bistro  0.03
7          Food Truck  0.03
8       Burrito Place  0.03
9    Sushi Restaurant  0.03


----Carnegie Hill----
                  venue  freq
0           Pizza Place  0.11
1      Sushi Restaurant  0.10
2                Bakery  0.08
3                  Café  0.08
4    Italian Restaurant  0.07
5    Mexican Restaurant  0.04
6   Japanese Restaurant  0.04
7     French Restaurant  0.04
8            Food Truck  0.03
9  Fast Food Restaurant  0.03


----Central Harlem----
                             venue  freq
0              Fried Chicken Joint  0.09
1                    Deli / Bodega  0.09
2             Caribbean Restaurant  0.07
3               African Restaurant  0.07
4               Seafood Restaurant  0.07
5  Southern / Soul Food Restaurant  0.07


In [138]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [139]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City           Pizza Place    Chinese Restaurant   
1      Carnegie Hill           Pizza Place      Sushi Restaurant   
2     Central Harlem   Fried Chicken Joint         Deli / Bodega   
3            Chelsea     French Restaurant                Bakery   
4          Chinatown    Chinese Restaurant                Bakery   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Sandwich Place            Donut Shop            Food Court   
1                   Café                Bakery    Italian Restaurant   
2     African Restaurant    Seafood Restaurant  Caribbean Restaurant   
3    American Restaurant                  Café    Italian Restaurant   
4  Vietnamese Restaurant   Dumpling Restaurant     Hotpot Restaurant   

             6th Most Common Venue 7th Most Common Venue  \
0                     Burger Joint                Bistro   
1                French Restaurant    Mexican Restaurant   
2  Southern / Soul Food Restaurant    Chinese Restaurant   
3              Japanese Restaurant           Pizza Place   
4               Mexican Restaurant   American Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0            Restaurant    Seafood Restaurant     Mexican Restaurant  
1   Japanese Restaurant    Chinese Restaurant      Indian Restaurant  
2            Restaurant   American Restaurant            Pizza Place  
3    Mexican Restaurant        Sandwich Place     Seafood Restaurant  
4   Shanghai Restaurant      Malay Restaurant            Pizza Place

## Grab K Means clusters

In [140]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 0, 1, 1, 2, 2, 0, 1, 1], dtype=int32)

In [141]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               4   
1  Manhattan           Chinatown  40.715618 -73.994279               1   
2  Manhattan  Washington Heights  40.851903 -73.936900               0   
3  Manhattan              Inwood  40.867684 -73.921210               0   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               0   

  1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue  \
0        Sandwich Place   American Restaurant            Pizza Place   
1    Chinese Restaurant                Bakery  Vietnamese Restaurant   
2           Pizza Place    Chinese Restaurant          Deli / Bodega   
3                  Café    Mexican Restaurant             Restaurant   
4         Deli / Bodega           Pizza Place     Mexican Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                 Diner            Steakhouse           Snack Place   
1   Dumpling Restaurant     Hotpot Restaurant    Mexican Restaurant   
2                Bakery                  Café    Mexican Restaurant   
3           Pizza Place    Spanish Restaurant                Bakery   
4                  Café            Donut Shop    Chinese Restaurant   

  7th Most Common Venue      8th Most Common Venue 9th Most Common Venue  \
0                Bakery         Seafood Restaurant            Donut Shop   
1   American Restaurant        Shanghai Restaurant      Malay Restaurant   
2            Donut Shop  Latin American Restaurant    Spanish Restaurant   
3    Chinese Restaurant       Caribbean Restaurant  Fast Food Restaurant   
4        Sandwich Place           Sushi Restaurant   Fried Chicken Joint   

      10th Most Common Venue  
0              Deli / Bodega  
1                Pizza Place  
2           Sushi Restaurant  
3            Thai Restaurant  
4  Latin American Restaurant

## Map Manhattan Clusters

In [142]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [169]:
plt.savefig('map_clusters.jpg', dpi=300)

<Figure size 432x288 with 0 Axes>

In [152]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
2    Washington Heights           Pizza Place    Chinese Restaurant   
3                Inwood                  Café    Mexican Restaurant   
4      Hamilton Heights         Deli / Bodega           Pizza Place   
5        Manhattanville         Deli / Bodega    Chinese Restaurant   
6        Central Harlem   Fried Chicken Joint         Deli / Bodega   
7           East Harlem    Mexican Restaurant                Bakery   
11     Roosevelt Island         Deli / Bodega           Pizza Place   
20      Lower East Side           Pizza Place    Chinese Restaurant   
26  Morningside Heights         Deli / Bodega            Food Truck   
36           Tudor City                  Café         Deli / Bodega   

   3rd Most Common Venue      4th Most Common Venue 5th Most Common Venue  \
2          Deli / Bodega                     Bakery                  Café   
3             Restaurant                Pizza Place    Spanish Restaurant   
4     Mexican Restaurant                       Café            Donut Shop   
5     Seafood Restaurant         Mexican Restaurant      Sushi Restaurant   
6     African Restaurant         Seafood Restaurant  Caribbean Restaurant   
7            Pizza Place  Latin American Restaurant         Deli / Bodega   
11      Greek Restaurant                       Food          Noodle House   
20      Ramen Restaurant                       Café         Deli / Bodega   
26          Burger Joint                Pizza Place    Chinese Restaurant   
36           Pizza Place         Mexican Restaurant      Sushi Restaurant   

              6th Most Common Venue 7th Most Common Venue  \
2                Mexican Restaurant            Donut Shop   
3                            Bakery    Chinese Restaurant   
4                Chinese Restaurant        Sandwich Place   
5                    Sandwich Place    Italian Restaurant   
6   Southern / Soul Food Restaurant    Chinese Restaurant   
7                              Café       Thai Restaurant   
11               Chinese Restaurant     Kosher Restaurant   
20                           Bakery        Sandwich Place   
26                             Café   American Restaurant   
36                 Greek Restaurant   American Restaurant   

        8th Most Common Venue    9th Most Common Venue  \
2   Latin American Restaurant       Spanish Restaurant   
3        Caribbean Restaurant     Fast Food Restaurant   
4            Sushi Restaurant      Fried Chicken Joint   
5                      Bakery               Food Court   
6                  Restaurant      American Restaurant   
7              Sandwich Place       Spanish Restaurant   
11                       Café           Sandwich Place   
20         Mexican Restaurant                    Diner   
26         Mexican Restaurant  New American Restaurant   
36           Asian Restaurant               Bagel Shop   

       10th Most Common Venue  
2            Sushi Restaurant  
3             Thai Restaurant  
4   Latin American Restaurant  
5        Fast Food Restaurant  
6                 Pizza Place  
7                  Steakhouse  
11        Japanese Restaurant  
20        Japanese Restaurant  
26             Sandwich Place  
36                 Restaurant

In [148]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
1            Chinatown    Chinese Restaurant                Bakery   
9            Yorkville    Italian Restaurant           Pizza Place   
15             Midtown   American Restaurant        Sandwich Place   
16         Murray Hill        Sandwich Place   Japanese Restaurant   
17             Chelsea     French Restaurant                Bakery   
19        East Village           Pizza Place    Mexican Restaurant   
22        Little Italy    Chinese Restaurant    Italian Restaurant   
25    Manhattan Valley    Mexican Restaurant           Pizza Place   
27            Gramercy    Italian Restaurant            Bagel Shop   
28   Battery Park City           Pizza Place    Chinese Restaurant   
29  Financial District        Sandwich Place           Salad Place   
30       Carnegie Hill           Pizza Place      Sushi Restaurant   
31                Noho    Italian Restaurant           Pizza Place   
33       Midtown South     Korean Restaurant                Bakery   
34        Sutton Place    Italian Restaurant            Bagel Shop   

       3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
1      Vietnamese Restaurant   Dumpling Restaurant          Hotpot Restaurant   
9           Sushi Restaurant         Deli / Bodega        Japanese Restaurant   
15              Burger Joint            Food Truck        Japanese Restaurant   
16  Mediterranean Restaurant          Burger Joint                Salad Place   
17       American Restaurant                  Café         Italian Restaurant   
19     Vietnamese Restaurant   Japanese Restaurant         Italian Restaurant   
22                    Bakery                  Café   Mediterranean Restaurant   
25         French Restaurant                  Café  Latin American Restaurant   
27             Deli / Bodega           Pizza Place            Thai Restaurant   
28            Sandwich Place            Donut Shop                 Food Court   
29               Pizza Place                  Café         Italian Restaurant   
30                      Café                Bakery         Italian Restaurant   
31       Japanese Restaurant    Mexican Restaurant             Sandwich Place   
33       Japanese Restaurant   American Restaurant                Salad Place   
34               Pizza Place   American Restaurant          Indian Restaurant   

            6th Most Common Venue 7th Most Common Venue  \
1              Mexican Restaurant   American Restaurant   
9                           Diner                Bakery   
15                     Steakhouse           Pizza Place   
16                    Pizza Place    Mexican Restaurant   
17            Japanese Restaurant           Pizza Place   
19  Vegetarian / Vegan Restaurant     Korean Restaurant   
22                    Pizza Place    Seafood Restaurant   
25                Thai Restaurant         Deli / Bodega   
27             Mexican Restaurant   American Restaurant   
28                   Burger Joint                Bistro   
29            American Restaurant         Deli / Bodega   
30              French Restaurant    Mexican Restaurant   
31              French Restaurant                  Café   
33                           Café          Burger Joint   
34               Asian Restaurant      Sushi Restaurant   

    8th Most Common Venue 9th Most Common Venue   10th Most Common Venue  
1     Shanghai Restaurant      Malay Restaurant              Pizza Place  
9      Mexican Restaurant    Chinese Restaurant           Sandwich Place  
15       Sushi Restaurant      Cuban Restaurant                     Café  
16     Chinese Restaurant         Deli / Bodega          Thai Restaurant  
17     Mexican Restaurant        Sandwich Place       Seafood Restaurant  
19                   Café   American Restaurant        French Restaurant  
22        Thai Restaurant        Sandwich Place    Vietnamese Restaurant  
25      Indian Restaurant   Szechuan Restaurant

In [149]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
8     Upper East Side    Italian Restaurant      American Restaurant   
10         Lenox Hill    Italian Restaurant         Sushi Restaurant   
12    Upper West Side    Italian Restaurant        Indian Restaurant   
13     Lincoln Square                  Café               Food Truck   
14            Clinton    Italian Restaurant            Deli / Bodega   
18  Greenwich Village    Italian Restaurant         Sushi Restaurant   
21            Tribeca    Italian Restaurant      American Restaurant   
23               Soho    Italian Restaurant        French Restaurant   
24       West Village    Italian Restaurant  New American Restaurant   
32       Civic Center    Italian Restaurant        French Restaurant   
35         Turtle Bay    Italian Restaurant                     Café   
38           Flatiron    Italian Restaurant                     Café   
39       Hudson Yards   American Restaurant                     Café   

       3rd Most Common Venue     4th Most Common Venue  \
8                Pizza Place                    Bakery   
10               Pizza Place             Deli / Bodega   
12  Mediterranean Restaurant               Pizza Place   
13        Italian Restaurant       American Restaurant   
14       American Restaurant                Restaurant   
18               Pizza Place                      Café   
21             Deli / Bodega                      Café   
23                      Café  Mediterranean Restaurant   
24       American Restaurant         French Restaurant   
32       American Restaurant            Sandwich Place   
35          Sushi Restaurant                Steakhouse   
38       American Restaurant       Japanese Restaurant   
39             Deli / Bodega        Italian Restaurant   

      5th Most Common Venue     6th Most Common Venue  \
8         French Restaurant                     Diner   
10             Burger Joint                      Café   
12                   Bakery                      Café   
13        French Restaurant               Pizza Place   
14           Sandwich Place        Chinese Restaurant   
18        French Restaurant            Sandwich Place   
21             Burger Joint            Sandwich Place   
23      American Restaurant            Sandwich Place   
24              Pizza Place         Indian Restaurant   
32                   Bakery             Deli / Bodega   
35            Deli / Bodega               Pizza Place   
38  New American Restaurant  Mediterranean Restaurant   
39          Thai Restaurant                Restaurant   

            7th Most Common Venue     8th Most Common Venue  \
8              Mexican Restaurant          Sushi Restaurant   
10            American Restaurant        Mexican Restaurant   
12                 Breakfast Spot                Restaurant   
13                         Bakery  Mediterranean Restaurant   
14             Mexican Restaurant               Pizza Place   
18       Mediterranean Restaurant       American Restaurant   
21               Greek Restaurant                    Bakery   
23                         Bakery        Chinese Restaurant   
24             Mexican Restaurant                 Gastropub   
32              Indian Restaurant          Sushi Restaurant   
35               Asian Restaurant            Sandwich Place   
38  Vegetarian / Vegan Restaurant          Sushi Restaurant   
39               Asian Restaurant          Greek Restaurant   

   9th Most Common Venue     10th Most Common Venue  
8         Sandwich Place                Salad Place  
10    Turkish Restaurant                     Bakery  
12      Sushi Restaurant  Middle Eastern Restaurant  
13    Chinese Restaurant              Deli / Bodega  
14                  Café            Thai Restaurant  
18    Chinese Restaurant          Indian Restaurant  
21     French Restaurant                 Poke Place  
23    Seafood Restaurant                Pizza Place  
24    Seafood Resta

In [150]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37  Stuyvesant Town         Deli / Bodega        Sandwich Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
37                Bistro     German Restaurant                Bakery   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
37  Fast Food Restaurant                  Food     Fish & Chips Shop   

   9th Most Common Venue 10th Most Common Venue  
37   Filipino Restaurant     Falafel Restaurant

In [151]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Marble Hill        Sandwich Place   American Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Pizza Place                 Diner            Steakhouse   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Snack Place                Bakery    Seafood Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0            Donut Shop          Deli / Bodega

## Grab only Italian Restaurant category

In [153]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?=&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
           radius, 
            LIMIT,
        "4bf58dd8d48988d110941735") #Food only category ID
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

In [154]:
# type your answer here

manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


In [156]:
print(manhattan_venues.shape)
manhattan_venues.head()

(893, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551              -73.910660   
1  Marble Hill              40.876551              -73.910660   
2    Chinatown              40.715618              -73.994279   
3    Chinatown              40.715618              -73.994279   
4    Chinatown              40.715618              -73.994279   

                        Venue  Venue Latitude  Venue Longitude  \
0                    Arturo's       40.874412       -73.910271   
1               Tibbett Diner       40.880404       -73.908937   
2          Di Palo Fine Foods       40.719148       -73.996577   
3                      Bacaro       40.714468       -73.991589   
4  Paesano of Mulberry Street       40.718658       -73.997636   

       Venue Category  
0  Italian Restaurant  
1               Diner  
2        Gourmet Shop  
3  Italian Restaurant  
4  Italian Restaurant

In [157]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       18                      18     18   
Carnegie Hill                           26                      26     26   
Central Harlem                           1                       1      1   
Chelsea                                 26                      26     26   
Chinatown                               46                      46     46   
Civic Center                            29                      29     29   
Clinton                                 36                      36     36   
East Harlem                              2                       2      2   
East Village                            38                      38     38   
Financial District                      50                      50     50   
Flatiron                                47                      47     47   
Gramercy                                15                      15     15   
Greenwich Village                       54                      54     54   
Hamilton Heights                         7                       7      7   
Hudson Yards                            10                      10     10   
Inwood                                   3                       3      3   
Lenox Hill                              25                      25     25   
Lincoln Square                          12                      12     12   
Little Italy                            57                      57     57   
Lower East Side                          8                       8      8   
Manhattan Valley                        12                      12     12   
Manhattanville                           2                       2      2   
Marble Hill                              2                       2      2   
Midtown                                 36                      36     36   
Midtown South                           32                      32     32   
Morningside Heights                      5                       5      5   
Murray Hill                             28                      28     28   
Noho                                    47                      47     47   
Soho                                    53                      53     53   
Sutton Place                            22                      22     22   
Tribeca                                 20                      20     20   
Tudor City                               5                       5      5   
Turtle Bay                              19                      19     19   
Upper East Side                         23                      23     23   
Upper West Side                         16                      16     16   
Washington Heights                       2                       2      2   
West Village                            38                      38     38   
Yorkville                               21                      21     21   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                18               18              18  
Carnegie Hill                    26               26              26  
Central Harlem                    1                1               1  
Chelsea                          26               26              26  
Chinatown                        46               46              46  
Civic Center                     29               29              29  
Clinton                          36               36              36  
East Harlem                       2                2               2  
East Village                     38               38              38  
Financial District               50               50              50  
Flatiron                         47               47              47  
Gramercy         

In [158]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 32 uniques categories.


In [160]:
manhattan_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Marble Hill              40.876551              -73.910660   
1  Marble Hill              40.876551              -73.910660   
2    Chinatown              40.715618              -73.994279   
3    Chinatown              40.715618              -73.994279   
4    Chinatown              40.715618              -73.994279   

                        Venue  Venue Latitude  Venue Longitude  \
0                    Arturo's       40.874412       -73.910271   
1               Tibbett Diner       40.880404       -73.908937   
2          Di Palo Fine Foods       40.719148       -73.996577   
3                      Bacaro       40.714468       -73.991589   
4  Paesano of Mulberry Street       40.718658       -73.997636   

       Venue Category  
0  Italian Restaurant  
1               Diner  
2        Gourmet Shop  
3  Italian Restaurant  
4  Italian Restaurant

## Map Italian Restaurants

In [165]:
# create map of toronto using latitude and longitude values
ital_map = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, Neighborhood in zip(manhattan_venues['Neighborhood Latitude'], manhattan_venues['Neighborhood Longitude'], manhattan_venues['Neighborhood']):
    label = '[], []'.format(Neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.75,
        parse_html=False).add_to(ital_map)

In [166]:
ital_map

In [167]:
plt.savefig('ital_map.jpg', dpi=300)

<Figure size 432x288 with 0 Axes>

In [168]:
plt.savefig('ital_map.pdf')

<Figure size 432x288 with 0 Axes>